In [1]:
import requests

# API endpoint
url = "https://api-samenmeten.rivm.nl/v1.0/Things"

try:
    # Send GET request
    response = requests.get(url)
    response.raise_for_status()  # Raise error for bad responses

    # Parse JSON response
    data = response.json()

    # Print the data (or save to a file for later processing)
    print(data)
except requests.exceptions.RequestException as e:
    print(f"Error retrieving data: {e}")


{'@iot.nextLink': 'https://api-samenmeten.rivm.nl/v1.0/Things?$top=200&$skip=200', 'value': [{'@iot.id': 9525, '@iot.selfLink': 'https://api-samenmeten.rivm.nl/v1.0/Things(9525)', 'name': 'LTD_82483', 'description': 'LTD_82483', 'properties': {'codegemeente': '794', 'knmicode': 'knmi_06375', 'nh3closecode': 'NL10131', 'nh3regiocode': 'NL10131', 'nh3stadcode': None, 'no2closecode': 'NL10131', 'no2regiocode': 'NL10131', 'no2stadcode': 'NL10236', 'owner': 'Luftdaten', 'pm10closecode': 'NL10131', 'pm10regiocode': 'NL10131', 'pm10stadcode': 'NL10236', 'pm25closecode': 'NL10131', 'pm25regiocode': 'NL10131', 'pm25stadcode': 'NL10741', 'project': 'Luftdaten'}, 'Locations@iot.navigationLink': 'https://api-samenmeten.rivm.nl/v1.0/Things(9525)/Locations', 'Datastreams@iot.navigationLink': 'https://api-samenmeten.rivm.nl/v1.0/Things(9525)/Datastreams', 'HistoricalLocations@iot.navigationLink': 'https://api-samenmeten.rivm.nl/v1.0/Things(9525)/HistoricalLocations'}, {'@iot.id': 9524, '@iot.selfLink

In [2]:
import requests

BASE_URL = "https://api-samenmeten.rivm.nl/v1.0"

def fetch_things():
    url = f"{BASE_URL}/Things"
    response = requests.get(url)
    response.raise_for_status()
    return response.json()

def fetch_datastreams(thing_id):
    url = f"{BASE_URL}/Things({thing_id})/Datastreams"
    response = requests.get(url)
    response.raise_for_status()
    return response.json()

def fetch_observations(datastream_id):
    url = f"{BASE_URL}/Datastreams({datastream_id})/Observations"
    response = requests.get(url)
    response.raise_for_status()
    return response.json()

# Example usage
things = fetch_things()
for thing in things["value"]:
    print(f"Thing: {thing['name']}")
    datastreams = fetch_datastreams(thing["@iot.id"])
    for ds in datastreams["value"]:
        print(f"  Datastream: {ds['name']}")
        observations = fetch_observations(ds["@iot.id"])
        for obs in observations["value"]:
            print(f"    Observation: {obs['result']}")


Thing: LTD_82483
  Datastream: LTD_82483-6-pres
    Observation: 1030.54
    Observation: 1031.21
    Observation: 1031.45
    Observation: 1031.2
  Datastream: LTD_82483-6-rh
    Observation: 65.79
    Observation: 65.27
    Observation: 65.61
    Observation: 64.6
  Datastream: LTD_82483-6-temp
    Observation: 15.33
    Observation: 15.17
    Observation: 14.53
    Observation: 14.29
  Datastream: LTD_82483-2-pm10_kal
    Observation: 3.828
    Observation: 3.116
    Observation: 1.764
    Observation: 3.105
  Datastream: LTD_82483-2-pm10
    Observation: 4.96
    Observation: 4.31
    Observation: 4.12
    Observation: 4.15
  Datastream: LTD_82483-2-pm25_kal
    Observation: 3.198
    Observation: 2.314
    Observation: 2.16
    Observation: 3.77
  Datastream: LTD_82483-2-pm25
    Observation: 2.82
    Observation: 2.6
    Observation: 2.61
    Observation: 2.74
Thing: MJS_1000
  Datastream: MJS_1000-16-rh
    Observation: 21.08
    Observation: 22.79
    Observation: 38.25
    Obs

In [4]:
import requests
import datetime
import pandas as pd
import tempfile




# Step 1: Define API base URL
BASE_URL = "https://api-samenmeten.rivm.nl/v1.0/"

# Step 2: Find Things (devices/sensors)
things_response = requests.get(BASE_URL + "Things").json()
things = things_response['value']

# Step 3: Select a Thing (replace `thing_id` with the correct one)
thing_id = things[0]['@iot.id']  # Example: Pick the first sensor
datastreams_response = requests.get(f"{BASE_URL}Things({thing_id})/Datastreams").json()
datastream_id = datastreams_response['value'][0]['@iot.id']  # Example: Pick the first datastream

# Step 4: Query Observations for the last 15 days
start_date = (datetime.datetime.utcnow() - datetime.timedelta(days=15)).isoformat() + "Z"
end_date = datetime.datetime.utcnow().isoformat() + "Z"
observations_url = f"{BASE_URL}Datastreams({datastream_id})/Observations"
params = {"$filter": f"phenomenonTime ge {start_date} and phenomenonTime le {end_date}"}
observations_response = requests.get(observations_url, params=params).json()

# Step 5: Parse and save the data
observations = observations_response['value']
data = [{"timestamp": obs['phenomenonTime'], "value": obs['result']} for obs in observations]
df = pd.DataFrame(data)
# df.to_csv("sensor_data.csv", index=False)
with tempfile.NamedTemporaryFile(delete=False, suffix=".csv") as temp_file:
    temp_path = temp_file.name
    df.to_csv(temp_path, index=False)
    print(f"Data saved temporarily at {temp_path}")

print("Data saved to sensor_data.csv!")


Data saved temporarily at /var/folders/bq/5f7dchhj4612jj76hb16wtq00000gn/T/tmpr75cw7sw.csv
Data saved to sensor_data.csv!


/var/folders/bq/5f7dchhj4612jj76hb16wtq00000gn/T/ipykernel_43576/277945589.py:22: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  start_date = (datetime.datetime.utcnow() - datetime.timedelta(days=15)).isoformat() + "Z"
/var/folders/bq/5f7dchhj4612jj76hb16wtq00000gn/T/ipykernel_43576/277945589.py:23: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  end_date = datetime.datetime.utcnow().isoformat() + "Z"


In [6]:
import requests
import datetime
import pandas as pd

# Base API URL
BASE_URL = "https://api-samenmeten.rivm.nl/v1.0/"
datastream_id = "YOUR_DATASTREAM_ID"  # Replace with actual ID

# Extended timeframe
start_date = (datetime.datetime.utcnow() - datetime.timedelta(days=30)).isoformat() + "Z"
end_date = datetime.datetime.utcnow().isoformat() + "Z"

# Query Observations with pagination
observations_url = f"{BASE_URL}Datastreams({datastream_id})/Observations"
params = {"$filter": f"phenomenonTime ge {start_date} and phenomenonTime le {end_date}"}
observations = []

while observations_url:
    response = requests.get(observations_url, params=params).json()
    observations.extend(response.get('value', []))
    observations_url = response.get('@iot.nextLink', None)

# Parse data into DataFrame
data = [{"timestamp": obs['phenomenonTime'], "value": obs['result']} for obs in observations]
df = pd.DataFrame(data)

# Save or display results
print(df)


Empty DataFrame
Columns: []
Index: []


/var/folders/bq/5f7dchhj4612jj76hb16wtq00000gn/T/ipykernel_43576/2782462136.py:10: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  start_date = (datetime.datetime.utcnow() - datetime.timedelta(days=30)).isoformat() + "Z"
/var/folders/bq/5f7dchhj4612jj76hb16wtq00000gn/T/ipykernel_43576/2782462136.py:11: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  end_date = datetime.datetime.utcnow().isoformat() + "Z"


In [13]:
import requests
from datetime import datetime, timedelta

# Define API base and time range
BASE_URL = "https://api-samenmeten.rivm.nl/v1.0"
end_date = datetime.utcnow()
start_date = end_date - timedelta(days=15)
start_date_str = start_date.isoformat() + "Z"
end_date_str = end_date.isoformat() + "Z"

# Example: Fetch observations for a specific Datastream ID
datastream_id = "47523"  # Replace with actual ID
url = f"{BASE_URL}/Datastreams({datastream_id})/Observations"
params = {
    "$filter": f"phenomenonTime ge {start_date_str} and phenomenonTime le {end_date_str}"
}

response = requests.get(url, params=params)
if response.status_code == 200:
    data = response.json()
    print(data)
else:
    print("Error:", response.status_code, response.text)


{'@iot.nextLink': 'https://api-samenmeten.rivm.nl/v1.0/Datastreams(47523)/Observations?$filter=phenomenonTime+ge+2024-11-14T13%3A17%3A26.995211Z+and+phenomenonTime+le+2024-11-29T13%3A17%3A26.995211Z&$top=200&$skip=200', 'value': [{'@iot.id': 541718973, '@iot.selfLink': 'https://api-samenmeten.rivm.nl/v1.0/Observations(541718973)', 'phenomenonTime': '2024-11-29T12:00:00.000Z', 'result': 7.29, 'Datastream@iot.navigationLink': 'https://api-samenmeten.rivm.nl/v1.0/Observations(541718973)/Datastream', 'FeatureOfInterest@iot.navigationLink': 'https://api-samenmeten.rivm.nl/v1.0/Observations(541718973)/FeatureOfInterest', 'resultTime': None}, {'@iot.id': 541706091, '@iot.selfLink': 'https://api-samenmeten.rivm.nl/v1.0/Observations(541706091)', 'phenomenonTime': '2024-11-29T11:00:00.000Z', 'result': 6.63, 'Datastream@iot.navigationLink': 'https://api-samenmeten.rivm.nl/v1.0/Observations(541706091)/Datastream', 'FeatureOfInterest@iot.navigationLink': 'https://api-samenmeten.rivm.nl/v1.0/Observa

/var/folders/bq/5f7dchhj4612jj76hb16wtq00000gn/T/ipykernel_43576/3280052958.py:6: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  end_date = datetime.utcnow()


In [11]:
import requests

# Base URL for the API
BASE_URL = "https://api-samenmeten.rivm.nl/v1.0"

# Fetch Datastreams
response = requests.get(f"{BASE_URL}/Datastreams")
if response.status_code == 200:
    data = response.json()
    for stream in data.get("value", []):
        print(f"Datastream ID: {stream['@iot.id']}, Name: {stream['name']}")
else:
    print("Error fetching Datastreams:", response.status_code, response.text)


Datastream ID: 47722, Name: LTD_82483-6-pres
Datastream ID: 47721, Name: LTD_82483-6-rh
Datastream ID: 47720, Name: LTD_82483-6-temp
Datastream ID: 47719, Name: LTD_82483-2-pm10_kal
Datastream ID: 47718, Name: LTD_82483-2-pm10
Datastream ID: 47717, Name: LTD_82483-2-pm25_kal
Datastream ID: 47716, Name: LTD_82483-2-pm25
Datastream ID: 47715, Name: MJS_1000-16-rh
Datastream ID: 47714, Name: MJS_1000-16-temp
Datastream ID: 47713, Name: MJS_1000-12-pm25_kal
Datastream ID: 47712, Name: MJS_1000-12-pm25
Datastream ID: 47711, Name: SSK_PM017-2-pm10_kal
Datastream ID: 47710, Name: SSK_PM017-2-pm10
Datastream ID: 47709, Name: SSK_PM017-12-pm25_kal
Datastream ID: 47708, Name: SSK_PM017-12-pm25
Datastream ID: 47707, Name: SSK_PM016-2-pm10_kal
Datastream ID: 47706, Name: SSK_PM016-2-pm10
Datastream ID: 47705, Name: SSK_PM016-12-pm25_kal
Datastream ID: 47704, Name: SSK_PM016-12-pm25
Datastream ID: 47703, Name: SSK_PM011-2-pm10_kal
Datastream ID: 47702, Name: SSK_PM011-2-pm10
Datastream ID: 47701, N

In [12]:
thing_id = "47523"  # Replace with a valid Thing ID
response = requests.get(f"{BASE_URL}/Things({thing_id})/Locations")
if response.status_code == 200:
    print(response.json())
else:
    print("Error fetching Locations:", response.status_code, response.text)


{'value': []}


In [14]:
from datetime import datetime, timezone, timedelta

# Define the time range
end_date = datetime.now(timezone.utc)  # Use timezone-aware UTC datetime
start_date = end_date - timedelta(days=15)

# Convert to ISO 8601 strings
start_date_str = start_date.isoformat()
end_date_str = end_date.isoformat()

print("Start Date:", start_date_str)
print("End Date:", end_date_str)


Start Date: 2024-11-14T13:18:19.897069+00:00
End Date: 2024-11-29T13:18:19.897069+00:00


In [15]:
import requests

# API base URL and Datastream ID
BASE_URL = "https://api-samenmeten.rivm.nl/v1.0"
datastream_id = "47524"  # Replace with the actual Datastream ID

# Timestamps
start_date_str = "2024-11-14T13:18:19.897069+00:00"
end_date_str = "2024-11-29T13:18:19.897069+00:00"

# Construct the URL with the filter
url = f"{BASE_URL}/Datastreams({datastream_id})/Observations"
params = {
    "$filter": f"phenomenonTime ge {start_date_str} and phenomenonTime le {end_date_str}"
}

# Make the request
response = requests.get(url, params=params)
if response.status_code == 200:
    data = response.json()
    print("Fetched Observations:", data)
else:
    print("Error:", response.status_code, response.text)


Fetched Observations: {'@iot.nextLink': 'https://api-samenmeten.rivm.nl/v1.0/Datastreams(47524)/Observations?$filter=phenomenonTime+ge+2024-11-14T13%3A18%3A19.897069%2B00%3A00+and+phenomenonTime+le+2024-11-29T13%3A18%3A19.897069%2B00%3A00&$top=200&$skip=200', 'value': [{'@iot.id': 541720846, '@iot.selfLink': 'https://api-samenmeten.rivm.nl/v1.0/Observations(541720846)', 'phenomenonTime': '2024-11-29T12:00:00.000Z', 'result': 2.05, 'Datastream@iot.navigationLink': 'https://api-samenmeten.rivm.nl/v1.0/Observations(541720846)/Datastream', 'FeatureOfInterest@iot.navigationLink': 'https://api-samenmeten.rivm.nl/v1.0/Observations(541720846)/FeatureOfInterest', 'resultTime': None}, {'@iot.id': 541707958, '@iot.selfLink': 'https://api-samenmeten.rivm.nl/v1.0/Observations(541707958)', 'phenomenonTime': '2024-11-29T11:00:00.000Z', 'result': 2.3, 'Datastream@iot.navigationLink': 'https://api-samenmeten.rivm.nl/v1.0/Observations(541707958)/Datastream', 'FeatureOfInterest@iot.navigationLink': 'http

In [14]:
import requests
import csv
from datetime import datetime, timezone, timedelta

# API base URL and Datastream ID
BASE_URL = "https://api-samenmeten.rivm.nl/v1.0"
datastream_id = "47524"  # Replace with the actual Datastream ID

# # Timestamps
# start_date_str = "2022-11-29T13:18:19.897069+00:00"
# end_date_str = "2024-11-29T13:18:19.897069+00:00"

# # Define API base URL and parameters
# BASE_URL = "https://api-samenmeten.rivm.nl/v1.0"
# datastream_id = "<Valid_Datastream_ID>"  # Replace with a valid Datastream ID

# Define time range
end_date = datetime.now(timezone.utc)
start_date = end_date - timedelta(days=365)
start_date_str = start_date.isoformat()
end_date_str = end_date.isoformat()

# API URL and query parameters
url = f"{BASE_URL}/Datastreams({datastream_id})/Observations"




for i in range(10):
    params = {
        "$filter": f"phenomenonTime ge {start_date_str} and phenomenonTime le {end_date_str}",
        "$top": "200",
        "$skip" : f"{200*i}"
    }

    # Make the API request
    response = requests.get(url, params=params)

    if response.status_code == 200:
        data = response.json().get("value", [])
        # Save to CSV
        with open("observations.csv", mode="a", newline="") as file:
            writer = csv.writer(file)
            # Write header
            writer.writerow(["phenomenonTime", "result"])
            # Write data rows
            for observation in data:
                writer.writerow([observation["phenomenonTime"], observation["result"]])
        print("Data saved to 'observations.csv'")
    else:
        print("Error:", response.status_code, response.text)


Data saved to 'observations.csv'
Data saved to 'observations.csv'
Data saved to 'observations.csv'
Data saved to 'observations.csv'
Data saved to 'observations.csv'
Data saved to 'observations.csv'
Data saved to 'observations.csv'
Data saved to 'observations.csv'
Data saved to 'observations.csv'
Data saved to 'observations.csv'


In [13]:
end_date_str

'2024-11-29T13:29:27.409804+00:00'

In [ ]:
# 2024-11-29T13:00:00.000Z
# 2024-11-29T03:00:00.000Z

In [15]:
git@github.com:aryastark1614/UrbanComputingProject.git

SyntaxError: illegal target for annotation (884510766.py, line 1)